# 代码提前声明  （用于做实验）
写代码坚持以下原则：

    *保证高内聚、低耦合的特性，各小块之间均是相互独立，把每个部分集成在一起，随时可以当做不上分点注释掉
    
    *把基本步骤分解开来，数据处理，模型整理都当做可选的方案，整体的可维护性最优
    
    *记住代码的层次、可维护性 是首当其冲，有好的体系下来，就算再难的问题，也能按照大佬模式逐个突破。
    
    *随手ctrl+s，麻蛋这个jupyter太坑了，不会自动保存，如果你reload之前不管过久的代码都没了

# 前置思考方案
    1.特征预处理
       *补缺失：对重要度大的特征进行缺失值补充
       *异常值去除
    ......
    2.单模型尝试
       *lightGBM
       *Catboost
    ......

In [203]:
#################     引包   #####################
import numpy as np
import pandas as pd
from pandas import DataFrame
from pandas import Series
import matplotlib
import matplotlib.pyplot as plt
import lightgbm as lgb
import operator
import time
import xgboost as xgb

%matplotlib inline

# 一.数据预处理

# ----------------------         1.数据读取        -------------------------

In [52]:
# 读取文件
train_xy = pd.read_csv("../data/train_xy.csv",header=0,sep=",")
train_x = pd.read_csv("../data/train_x.csv",header=0,sep=",")
test_all = pd.read_csv("../data/test_all.csv",header=0,sep=",")
print(train_xy.shape)
print(train_x.shape)
print(test_all.shape)
train = train_xy.copy()
test = test_all.copy()
test['y'] = -1
print('训练集的特征列train：',train.columns)
print('训练集的特征列test：',test.columns)
# 合并一下train 和 test
data = pd.concat([train,test],axis = 0) # train_xy，test_all索引上连接
print(train.shape)
print(test.shape)
print(data.shape)
print('训练集的特征列：',data.columns)

(15000, 160)
(10000, 159)
(10000, 159)
训练集的特征列train： Index(['cust_id', 'cust_group', 'y', 'x_1', 'x_2', 'x_3', 'x_4', 'x_5', 'x_6',
       'x_7',
       ...
       'x_148', 'x_149', 'x_150', 'x_151', 'x_152', 'x_153', 'x_154', 'x_155',
       'x_156', 'x_157'],
      dtype='object', length=160)
训练集的特征列test： Index(['cust_id', 'cust_group', 'x_1', 'x_2', 'x_3', 'x_4', 'x_5', 'x_6',
       'x_7', 'x_8',
       ...
       'x_149', 'x_150', 'x_151', 'x_152', 'x_153', 'x_154', 'x_155', 'x_156',
       'x_157', 'y'],
      dtype='object', length=160)
(15000, 160)
(10000, 160)
(25000, 160)
训练集的特征列： Index(['cust_group', 'cust_id', 'x_1', 'x_10', 'x_100', 'x_101', 'x_102',
       'x_103', 'x_104', 'x_105',
       ...
       'x_91', 'x_92', 'x_93', 'x_94', 'x_95', 'x_96', 'x_97', 'x_98', 'x_99',
       'y'],
      dtype='object', length=160)


d:\python35\lib\site-packages\ipykernel_launcher.py:14: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  


# ----------------------         2.删除高缺特征        -------------------------
*此处也加入了对缺失统计特征的构建

In [53]:


# 删除一些不必要的特征（噪音、缺失严重、单值、重复等）     删除掉训练集和测试集中同时缺失大于百分之95的
# train ,test 分开分析 
# 处理一下缺失值严重的特征列，删除
def get_nan_feature(train,rate = 0.95):
    total_num = train.shape[0]
    train_nan_feats = []
    for i in range(157):
        feat = 'x_' + str(i+1)
        nan_num = train.loc[train[feat]==-99,:].shape[0]
        nan_rate = nan_num / float(total_num) 
        
        if nan_rate == 1.0:                    # 只有nan
            train_nan_feats.append(feat)
        if nan_rate > rate:                    # 有缺失值 nan,而且缺失严重
            if len(train[feat].unique()) == 2: # 只有nan + 一个其他值
                train_nan_feats.append(feat)

    print("一共有 %d 个特征列的缺失值严重，超过%f "%(len(train_nan_feats),rate))
    return train_nan_feats

train_nan_feats = get_nan_feature(train)
test_nan_feats = get_nan_feature(test)
print("缺失严重的特征：train =?= test------",np.all(train_nan_feats == test_nan_feats))

# 对这些特征取并集:28个
nan_feats = list(set(train_nan_feats) | set(test_nan_feats)) # 按照train | test的结果,并集，交集，A or B 都一样     并集方式的，其实可以多尝试
print('严重缺失的特征有 %d 个。'%(len(nan_feats)))

# 总的删除的特征（发现删重复的5个特征，效果不好，所以只删除28个缺失严重的特征,这是有尝试过得）
drop_feats = nan_feats 
print('一共删除的特征有 %d 个。'%(len(drop_feats)))
print(drop_feats)

# 删除缺失值严重的特征列
train = train.drop(drop_feats, axis = 1)
test = test.drop(drop_feats, axis = 1)
data = data.drop(drop_feats, axis = 1)
print(data.shape)
print(train.shape)
print(test.shape)
# 删除的特征，全部是特征重要性=0的特征，所以删除 = 原始的特征（不影响精确效果，但是可以减少噪音）
# 删除了x_92 , x_94 是数值型的，其他 24 个 全部是 类别型

print('训练集的特征列：',data.columns)

一共有 19 个特征列的缺失值严重，超过0.950000 
一共有 26 个特征列的缺失值严重，超过0.950000 
缺失严重的特征：train =?= test------ False
严重缺失的特征有 28 个。
一共删除的特征有 28 个。
['x_114', 'x_134', 'x_110', 'x_129', 'x_111', 'x_126', 'x_108', 'x_131', 'x_107', 'x_92', 'x_135', 'x_132', 'x_133', 'x_119', 'x_118', 'x_123', 'x_116', 'x_109', 'x_128', 'x_102', 'x_130', 'x_127', 'x_94', 'x_138', 'x_137', 'x_112', 'x_115', 'x_113']
(25000, 132)
(15000, 132)
(10000, 132)
训练集的特征列： Index(['cust_group', 'cust_id', 'x_1', 'x_10', 'x_100', 'x_101', 'x_103',
       'x_104', 'x_105', 'x_106',
       ...
       'x_9', 'x_90', 'x_91', 'x_93', 'x_95', 'x_96', 'x_97', 'x_98', 'x_99',
       'y'],
      dtype='object', length=132)


# ----------------------         3.对缺失特征做处理        -------------------------

   *此处还附加了将数值型特征进行排序并归一化处理，相当于做成了排序特征
   
   *也附加了构建缺失统计特征，并对缺失统计进行onehot编码，让其更稳定

   *挑选重要度大、缺失比较少的特征进行填充

In [54]:

# 对剩下的特征进行分析，分为数值型 、 类别型        (这里有疑问，难道默认0-94列特征是数值型特征吗，这很不合理啊)
numerical_features = []
categorical_features = []
for i in range(157):
    feat = "x_" + str(i+1)
    if feat not in drop_feats:
        if i <= 94: # 1-95
            numerical_features.append(feat)
        else:
            categorical_features.append(feat)
print("剩下的数值型特征：",len(numerical_features))
print("剩下的类别型特征：",len(categorical_features))

print('数值型特征为：',categorical_features)
print('数值型为：',data[categorical_features])
print('训练集的特征列：',data.columns)


剩下的数值型特征： 93
剩下的类别型特征： 36
数值型特征为： ['x_96', 'x_97', 'x_98', 'x_99', 'x_100', 'x_101', 'x_103', 'x_104', 'x_105', 'x_106', 'x_117', 'x_120', 'x_121', 'x_122', 'x_124', 'x_125', 'x_136', 'x_139', 'x_140', 'x_141', 'x_142', 'x_143', 'x_144', 'x_145', 'x_146', 'x_147', 'x_148', 'x_149', 'x_150', 'x_151', 'x_152', 'x_153', 'x_154', 'x_155', 'x_156', 'x_157']
数值型为：       x_96  x_97  x_98  x_99  x_100  x_101  x_103  x_104  x_105  x_106  ...    \
0        2     2     2     1      1      1    -99    -99    -99    -99  ...     
1        1     2     1     1      1      1    -99    -99    -99    -99  ...     
2        1     1     1     1      1      1    -99    -99    -99    -99  ...     
3        1     2     2     1      1      1    -99    -99    -99    -99  ...     
4        2     1     1     1      1      1    -99    -99    -99    -99  ...     
5        2     2     2     1      1      1    -99    -99    -99    -99  ...     
6        1     1     1     1      1      1    -99    -99    -99    -99  

In [55]:
# 统计每个样本缺失值的个数                  统计缺失样本数 构建统计特征
def get_nan_count(data,feats,bins = 7):
    df = data[feats].copy()
    df = df.replace(-99,np.nan)
    print('总列数:',df.shape[1])   #这列展示了每一行缺失的特征的数量
    print('每行非空列数:',df.count(axis = 1).values)   #这列展示了每一行缺失的特征的数量
    df['nan_count'] = df.shape[1] - df.count(axis = 1).values  # 列数 - 非nan数
    print('每行空列数:',df['nan_count'])   #这列展示了每一行缺失的特征的数量
    dummy = pd.get_dummies(pd.cut(df['nan_count'],bins),prefix = 'nan') #把每行空列数，做7分离散化再转one-hot编码 对缺失数据进行离散化,划分为7个区间,对于划分区间，这里根据空值情况来造dummies特征
    print(dummy.shape)
    res = pd.concat([data,dummy],axis = 1) # 合并到原来的数据
    print(res.shape)
    return res
# 在全部特征上面统计缺失值      新加入了对缺失值统计的7列
data = get_nan_count(data,data.columns.values,7)
print('训练集的特征列：',data.columns)

总列数: 132
每行非空列数: [ 84  85 120 ... 117  82  85]
每行空列数: 0       48
1       47
2       12
3       11
4       29
5       54
6       15
7       51
8       11
9       48
10      32
11      11
12      30
13      50
14      15
15      33
16      15
17      33
18      51
19      51
20      12
21      48
22      12
23      13
24      15
25      52
26      12
27      12
28      29
29      15
        ..
9970    15
9971    15
9972    14
9973    51
9974    51
9975    12
9976    11
9977    12
9978    48
9979    16
9980    15
9981    11
9982    15
9983    12
9984    51
9985    51
9986    15
9987    13
9988    14
9989    50
9990    14
9991    51
9992    12
9993    48
9994    15
9995    14
9996    11
9997    15
9998    50
9999    47
Name: nan_count, Length: 25000, dtype: int64
(25000, 7)
(25000, 139)
训练集的特征列： Index(['cust_group', 'cust_id', 'x_1', 'x_10', 'x_100', 'x_101', 'x_103',
       'x_104', 'x_105', 'x_106',
       ...
       'x_98', 'x_99', 'y', 'nan_(7.895, 23.0]', 'nan_(23.0, 38.0]',
       'n

In [56]:
# 获取缺失很少的数值型的特征         缺失少的数值型用均值
def get_little_nan_feats(df,numerical_features,rate = 0.1):
    total_num = df.shape[0]
    little_nan_feats = []
    for feat in numerical_features:
        nan_num = df.loc[df[feat]==-99,:].shape[0]
        nan_rate = nan_num / float(total_num) 
        if nan_rate <= rate:
            little_nan_feats.append(feat)
            #print("feature:",feat,"nan_num = ",nan_num,"nan_rate = ",nan_rate)
    print("一共有 %d 个特征列的缺失值较少，低于%f "%(len(little_nan_feats),rate))
    return little_nan_feats
little_nan_feats = get_little_nan_feats(data, numerical_features)
print("缺失较少的特征：",little_nan_feats)

print('训练集的特征列：',data.columns)
'''
# 对一些数值的特征进行平均值填充
for feat in little_nan_feats:
    data[feat] = data[feat].replace(-99,np.nan)
    data[feat] = data[feat].fillna(data[feat].mean())
'''# 对一些重要数值的特征进行平均值填充    (根据其特性吧，因为不是时序问题，线性差值肯定是不合适的。)





一共有 55 个特征列的缺失值较少，低于0.100000 
缺失较少的特征： ['x_1', 'x_2', 'x_39', 'x_40', 'x_41', 'x_42', 'x_43', 'x_44', 'x_45', 'x_46', 'x_47', 'x_48', 'x_49', 'x_50', 'x_51', 'x_52', 'x_53', 'x_54', 'x_55', 'x_56', 'x_57', 'x_58', 'x_59', 'x_60', 'x_61', 'x_62', 'x_63', 'x_64', 'x_65', 'x_66', 'x_67', 'x_68', 'x_69', 'x_70', 'x_71', 'x_72', 'x_73', 'x_74', 'x_75', 'x_76', 'x_77', 'x_78', 'x_79', 'x_80', 'x_81', 'x_82', 'x_83', 'x_84', 'x_85', 'x_86', 'x_87', 'x_88', 'x_89', 'x_90', 'x_91']
训练集的特征列： Index(['cust_group', 'cust_id', 'x_1', 'x_10', 'x_100', 'x_101', 'x_103',
       'x_104', 'x_105', 'x_106',
       ...
       'x_98', 'x_99', 'y', 'nan_(7.895, 23.0]', 'nan_(23.0, 38.0]',
       'nan_(38.0, 53.0]', 'nan_(53.0, 68.0]', 'nan_(68.0, 83.0]',
       'nan_(83.0, 98.0]', 'nan_(98.0, 113.0]'],
      dtype='object', length=139)


'\n# 对一些数值的特征进行平均值填充\nfor feat in little_nan_feats:\n    data[feat] = data[feat].replace(-99,np.nan)\n    data[feat] = data[feat].fillna(data[feat].mean())\n'

In [57]:
#对重要的特征进行填充，之后还会想着对着重要的特征利用其进行采样操作
imp_feat=['x_80','x_2','x_81','x_95','x_1','x_52','x_63','x_54','x_43','x_40','x_93','x_42','x_157','x_62','x_29','x_61','x_55']
print('假定的重要特征个数为：',len(imp_feat))
for feat in imp_feat[:10]:
    if feat in numerical_features: 
        print('进行填充吧')
        data[feat]=data[feat].replace(-99,np.nan)
        data[feat]=data[feat].fillna(data[feat].mean())
    if feat in categorical_features:  
        print('这是类别特征：',feat)
        
        
#确认下这些特征是否已经被填充好了
for feat in ['x_80','x_2','x_81','x_95','x_1','x_52']:
    nan_num = data.loc[data[feat]==-99,:].shape[0]
    print('缺失数量为：',nan_num)

假定的重要特征个数为： 17
进行填充吧
进行填充吧
进行填充吧
进行填充吧
进行填充吧
进行填充吧
进行填充吧
进行填充吧
进行填充吧
进行填充吧
缺失数量为： 0
缺失数量为： 0
缺失数量为： 0
缺失数量为： 0
缺失数量为： 0
缺失数量为： 0


In [58]:
# 对数值型的特征，处理为rank特征（鲁棒性好一点）     数值本身就代表大小的意思，这里构建排序特征并进行归一化，效果会更加鲁棒一些。

for feat in numerical_features:
    if feat not in imp_feat[:10]: #对均值填充后的列  不做rank排序，因为这样排序下来很多列是错的，咱们只是为了拟合分布
        #print('rank前：',data[feat])
        data[feat] = data[feat].rank() / float(data.shape[0]) # 排序，并且进行归一化        这样也行？
    #print('rank后：',data[feat])
print('训练集的特征列：',data.columns)

训练集的特征列： Index(['cust_group', 'cust_id', 'x_1', 'x_10', 'x_100', 'x_101', 'x_103',
       'x_104', 'x_105', 'x_106',
       ...
       'x_98', 'x_99', 'y', 'nan_(7.895, 23.0]', 'nan_(23.0, 38.0]',
       'nan_(38.0, 53.0]', 'nan_(53.0, 68.0]', 'nan_(68.0, 83.0]',
       'nan_(83.0, 98.0]', 'nan_(98.0, 113.0]'],
      dtype='object', length=139)


# ----------------------         4.数据采样处理        -------------------------

In [59]:
#这个方式可能效果不太好

# from imblearn.over_sampling import SMOTE       #过度抽样处理库SMOTE
# from imblearn.under_sampling import RandomUnderSampler
# #进行两种采样方式的处理，欠采样和过采样的处理，尝试在重要的10个特征上面进行采样，来获得标签
# #过采样处理\
# print('开始了,第一种方式(可选择：选择计算的距离依据是最重要的哪几个特征？ 往往更多的特征依据会起到更好的采样生成效果，可以多做尝试吧 )')
# x= data[['x_80','x_2','x_81','x_95','x_1','x_52','x_63','x_54','x_43']]
# feature_columns=[i for i in x.columns]
# y =data['y']
# #groupby_data_orginal = y.groupby('label').count()
# #print(x)
# #print(y)
# model_smote = SMOTE()  # 建立smote模型对象
# x_smote_resampled, y_smote_resampled = model_smote.fit_sample(x, y)
# x_smote_resampled = pd.DataFrame(x_smote_resampled, columns=feature_columns)
# y_smote_resampled = pd.DataFrame(y_smote_resampled, columns=['y'])
# smote_resampled = pd.concat([x_smote_resampled, y_smote_resampled], axis=1)
# groupby_data_smote = smote_resampled.groupby('y').count()
# smote_resampled.to_csv('./feature_data/经过过采样后的数据.csv')
# print(smote_resampled)

In [ ]:
#半监督学习 构造新样本


# 二.特征工程

# ----------------------         1.特征整理      -------------------------

In [60]:
######################################################      1.特征整理   #############################################

train = data.loc[data['y']!=-1,:] # train set
test = data.loc[data['y']==-1,:]  # test set
print(train.shape)
print(test.shape)
#print(train)
print('训练集的特征列：',train.columns)
# 获取特征列，去除id，group,y
no_features = ['cust_id','cust_group','y'] 
features = [feat for feat in train.columns.values if feat not in no_features]
print("所有特征的维度：",len(features))

(15000, 139)
(10000, 139)
训练集的特征列： Index(['cust_group', 'cust_id', 'x_1', 'x_10', 'x_100', 'x_101', 'x_103',
       'x_104', 'x_105', 'x_106',
       ...
       'x_98', 'x_99', 'y', 'nan_(7.895, 23.0]', 'nan_(23.0, 38.0]',
       'nan_(38.0, 53.0]', 'nan_(53.0, 68.0]', 'nan_(68.0, 83.0]',
       'nan_(83.0, 98.0]', 'nan_(98.0, 113.0]'],
      dtype='object', length=139)
所有特征的维度： 136


# ----------------------         2.构建交叉特征       -------------------------

In [61]:
######################################################        #############################################

#使用找到的还不错的特征，但是发现线上效果并不好，所以就不用了吧

#多项式特征，二次变换特征    变换特征基本没什么用
# train['all_index']=[i for i in range(0,15000)]
# train['x_80-x_63']=train['x_80']-train['x_63']
# train['x_80+x_64']=train['x_80']+train['x_64']
# train['x_80/x_63']=train['x_80']/train['x_63']

# train['x_95+x_93']=train['x_95']+train['x_42']
# train['x_80+x_93']=train['x_80']+train['x_42']
# train['x_63*x_93']=train['x_95']-train['x_42']
# train['x_63**2']=train['x_80']**1/2


# #test['all_index']=[i for i in range(0,10000)]

# test['x_95+x_93']=test['x_95']+test['x_42']
# test['x_80+x_93']=test['x_80']+test['x_42']
# test['x_63*x_93']=test['x_95']-test['x_42']
# test['x_63**2']=test['x_80']**1/2

# test['x_80-x_63']=test['x_80']-test['x_63']
# test['x_80+x_64']=test['x_80']+test['x_64']
# test['x_80/x_63']=test['x_80']/test['x_63']

# #这里，之前交叉特征根本没加入到训练里面尴尬
# features.extend(['x_95+x_93','x_80+x_93','x_63*x_93','x_63**2','x_80-x_63','x_80+x_64','x_80/x_63'])
# print(train.columns)

# ----------------------         3.特征分离       -------------------------

In [62]:

# 得到输入X ，输出y
#train=train.replace(-99,np.nan)#  尝试进行替换之后再训练看看效果（发现效果变差了）
#test=test.replace(-99,np.nan)#  尝试进行替换之后再训练看看效果（发现效果变差了）
train_id = train.pop('cust_id')
y = train['y'].values
X = train[features].values
print('X features :',features)
print("X shape:",X.shape)
print("y shape:",y.shape)

test_id = test.pop('cust_id')
test_data = test[features].values
print("test shape",test_data.shape)
print(train.columns)
train.to_csv('../feature_data/经过特征工程后的整个表.csv')
# X.to_csv('./feature_data/train_feature.csv')
# y.to_csv('./feature_data/train_label.csv')
print('训练集的特征列：',train.columns)

X features : ['x_1', 'x_10', 'x_100', 'x_101', 'x_103', 'x_104', 'x_105', 'x_106', 'x_11', 'x_117', 'x_12', 'x_120', 'x_121', 'x_122', 'x_124', 'x_125', 'x_13', 'x_136', 'x_139', 'x_14', 'x_140', 'x_141', 'x_142', 'x_143', 'x_144', 'x_145', 'x_146', 'x_147', 'x_148', 'x_149', 'x_15', 'x_150', 'x_151', 'x_152', 'x_153', 'x_154', 'x_155', 'x_156', 'x_157', 'x_16', 'x_17', 'x_18', 'x_19', 'x_2', 'x_20', 'x_21', 'x_22', 'x_23', 'x_24', 'x_25', 'x_26', 'x_27', 'x_28', 'x_29', 'x_3', 'x_30', 'x_31', 'x_32', 'x_33', 'x_34', 'x_35', 'x_36', 'x_37', 'x_38', 'x_39', 'x_4', 'x_40', 'x_41', 'x_42', 'x_43', 'x_44', 'x_45', 'x_46', 'x_47', 'x_48', 'x_49', 'x_5', 'x_50', 'x_51', 'x_52', 'x_53', 'x_54', 'x_55', 'x_56', 'x_57', 'x_58', 'x_59', 'x_6', 'x_60', 'x_61', 'x_62', 'x_63', 'x_64', 'x_65', 'x_66', 'x_67', 'x_68', 'x_69', 'x_7', 'x_70', 'x_71', 'x_72', 'x_73', 'x_74', 'x_75', 'x_76', 'x_77', 'x_78', 'x_79', 'x_8', 'x_80', 'x_81', 'x_82', 'x_83', 'x_84', 'x_85', 'x_86', 'x_87', 'x_88', 'x_89', 'x

In [65]:
train.to_csv('../feature_data/经过特征工程后的整个表.csv')


# 三.单模型方式

# ----------------------         1.Xgboost模型       -------------------------

In [168]:
#开始xgb的cv训练
# 采取分层采样
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import roc_auc_score
from xgboost import XGBClassifier
print("start：********************************")
start = time.time()

N = 5
skf = StratifiedKFold(n_splits=N,shuffle=True,random_state=2018)

auc_cv = []
pred_cv = []
for k,(train_in,test_in) in enumerate(skf.split(X,y)):
    X_train,X_test,y_train,y_test = X[train_in],X[test_in],\
                                    y[train_in],y[test_in]    
    # 模型参数
    params = {	'booster':'gbtree',
	'objective': 'binary:logistic',
	'early_stopping_rounds':100,
#     'gamma':0,#0.2 is ok
#     'max_depth':8,
# # 	'lambda':550,
    'subsample':0.7,
    'colsample_bytree':0.3,
    'min_child_weight':2.5, 
    'eta': 0.007,
	'seed':2018,
	'nthread':7}
    dtrain = xgb.DMatrix(X_train, label=y_train)
    dvali = xgb.DMatrix(X_test)
    model = xgb.train(params, dtrain, num_boost_round=800)
    predict = model.predict(dvali)
    print('预测出的结果1111：',predict)
    print('预测出的结果1111：',y_test)
    tmp_auc = roc_auc_score(y_test,predict)
    auc_cv.append(tmp_auc)
    print("valid auc:",tmp_auc)
    # test
    pred = model.predict(xgb.DMatrix(test_data))
    print('预测出的结果222：',predict)
    pred_cv.append(pred) 
    
    
    
#     xgb.plot_importance(model,max_num_features=20)
#     plt.title('xgb Feature Importance')
#     plt.xlabel('relative importance')
#     plt.show()

# K交叉验证的平均分数 
print('the cv information:')
print(auc_cv)
print('cv mean score',np.mean(auc_cv))

end = time.time()
print("......................run with time: ",(end - start) / 60.0 )
print("over:*********************************")

start：********************************
预测出的结果1111： [-2.5589669  -2.414111   -1.5141618  ... -0.5473174   0.86564034
 -0.87870944]
预测出的结果1111： [0 0 0 ... 1 1 1]
valid auc: 0.8154130783423577
预测出的结果222： [-2.5589669  -2.414111   -1.5141618  ... -0.5473174   0.86564034
 -0.87870944]
预测出的结果1111： [-2.2881072  -0.7315484  -2.5808716  ... -0.65460885 -0.8843206
 -0.49918967]
预测出的结果1111： [0 0 0 ... 1 1 1]
valid auc: 0.7868522063217168
预测出的结果222： [-2.2881072  -0.7315484  -2.5808716  ... -0.65460885 -0.8843206
 -0.49918967]
预测出的结果1111： [-2.6112583  -0.97374344 -2.1202111  ... -1.0726331  -1.4621875
  0.6798234 ]
预测出的结果1111： [0 0 0 ... 1 1 1]
valid auc: 0.8525633235094543
预测出的结果222： [-2.6112583  -0.97374344 -2.1202111  ... -1.0726331  -1.4621875
  0.6798234 ]
预测出的结果1111： [-2.426222  -2.8007689 -0.8920264 ...  1.9835185 -1.008568   1.3051045]
预测出的结果1111： [0 0 0 ... 1 1 1]
valid auc: 0.8416051408258135
预测出的结果222： [-2.426222  -2.8007689 -0.8920264 ...  1.9835185 -1.008568   1.3051045]
预测出的结果1111： [ 1

--------------------------------------------------------------------------------------------------------------------------------------
线下效果记录：（记住那些特征能够在线上涨分就作为使用的特征）


    [1]使用如下参数，cv效果是0.8095941001927958   (初版特征)
              'booster': 'gbtree',    
              'objective': 'binary:logistic',
              'eta': 0.02,
              'max_depth': 5,  # 4 3
              'colsample_bytree': 0.7,  # 0.8
              'subsample': 0.7,
              'min_child_weight': 9,  # 2 3
              'silent': 1
    [2]默认参数下，cv值是：0.6694547520305475
    
    
    [3]使用如下调参后的结果为0.8118425236460529   (初版特征)
              'booster': 'gbtree',
              'objective': 'binary:logistic',
              'eta': 0.02,
              'max_depth': 3,  # 4 3         (调出)
              'colsample_bytree': 0.7,  # 0.8
              'subsample': 0.5,              (调出)
              'min_child_weight': 9,  # 2 3
              'silent': 1
    [4]使用如下调参后的结果为0.814163899785226    (初版特征)
              'booster': 'gbtree',
              'objective': 'binary:logistic',
              'eta': 0.01,
              'max_depth': 3,  # 4 3
              'colsample_bytree': 0.5,  # 0.8
              'subsample': 0.5,
              'min_child_weight': 9,  # 2 3
              'silent': 1,
              'gamma': 0    
     [5]使用模型4与lightgbm模型(0.81952101)进行blend （前期放弃融合方案，做单模型计算，并且每个模型都要充分考虑过拟合的问题）
     0.7    0.3的权值分配  线下：0.8184459400734287     线上值：0.75182 （这个稳定性稍好点）
     0.6    0.4的权值分配  线下：0.818504121445845
     0.5    0.5的权值分配  线下：0.8182861386523573    
     0.9    0.1的权值分配  线下：0.8175251371900479
     与lighhtgbm模型（0.8211793803301299）结合线下：  
     0.7    0.3的权值分配  线下：0.8210557752290836     线上值：0.750+效果变差了
     [6]使用如下调参后的结果为0.8187509059471199    (初版特征)
     'booster':'gbtree',
	'objective': 'binary:logistic',
	'early_stopping_rounds':100,
    'subsample':0.7,
    'colsample_bytree':0.3,
    'min_child_weight':2.5, 
    'eta': 0.007,
	'seed':2018,
	'nthread':7
     注意：与高cv的线下分进行融合效果变差，说明调参调的过拟合了。
     ！！！！！！！！！！！！！！！！！！！！！！！！！！！！   不做模型调整了，   ！！！！！！！！！！！！！！！！！！！！
     [7]把-99替换下为nan,让模型自己去判断空值 在线下有点提升为0.8190473478328284
     [8]加入交叉特征，线下为0.8192969307017934  ，统计特征之间加入没效果，是自己加入方式不对，有问题，没有把列名实际加上去，程序逻辑写的出问题了。 线上有下降，那么交叉特征就干脆不用了
       train['x_80-x_63']=train['x_80']-train['x_63']
       train['x_80+x_64']=train['x_80']+train['x_64']
       train['x_80/x_63']=train['x_80']/train['x_63']
       train['x_95+x_93']=train['x_95']+train['x_42']
       train['x_80+x_93']=train['x_80']+train['x_42']
       train['x_63*x_93']=train['x_95']-train['x_42']
       train['x_63**2']=train['x_80']**1/2
   
     [9]使用上序号，能够让线下效果提升到0.9842626010230955，但是这样根本就不行哎，会在线上完全过拟合的，(用统计特征会降分，又过拟合了)
        train['all_index']=[i for i in range(0,15000)]
        train['x_80-x_63']=train['x_80']-train['x_63']
        train['x_80+x_64']=train['x_80']+train['x_64']
        train['x_80/x_63']=train['x_80']/train['x_63']

        train['x_95+x_93']=train['x_95']+train['x_42']
        train['x_80+x_93']=train['x_80']+train['x_42']
        train['x_63*x_93']=train['x_95']-train['x_42']
        train['x_63**2']=train['x_80']**1/2
     [10]原效果是0.8190，现在对最重要的10个特征进行填充，线下效果变成0.8190473478328284,发现并没有多大的效果，但是这种提分点可能是在xgboost中不敏感吧。
     [11]利用下之前比赛被人的参数尝试下吧，看效果怎么样  线下是0.8176944211826322，那就算了，既然效果不好就不用了吧
             	'booster':'gbtree',
    	'objective': 'rank:pairwise',
    	'scale_pos_weight': float(len(y)-sum(y))/float(sum(y)),
        'eval_metric': 'auc',
    	'gamma':0.1,
    	'max_depth':8,
    	'lambda':600,
        'subsample':0.6,
        'colsample_bytree':0.3,
        'min_child_weight':0.3, 
        'eta': 0.04,
    	'seed':1024,
    	'nthread':20
     
--------------------------------------------------------------------------------------------------------------------------------------

In [61]:
#生成预测结果
mean_auc = np.mean(auc_cv)
print("mean auc:",mean_auc)
filepath = 'result/xgb_'+ str(mean_auc)+'.csv' # 线下平均分数

# 转为array
res =  np.array(pred_cv)
print("总的结果：",res.shape)

# 最后结果，mean，max，min
r = res.mean(axis = 0)
print('result shape:',r.shape)

result = DataFrame()
result['cust_id'] = test_id
result['pred_prob'] = r
result.to_csv(filepath,index=False,sep=",")

mean auc: 0.8187509059471199
总的结果： (5, 10000)
result shape: (10000,)


In [ ]:
#xgb找参数（网格调参）
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.model_selection import GridSearchCV
from xgboost.sklearn import XGBClassifier
#使用网格搜索找最佳的参数
param_grid = {'gamma':[0,0.1,0.2,0.3,],'learning_rate':[0.01,0.02,0.03,0.04,],'colsample_bytree':[0.5,0.6,0.7,0.8],'subsample':[0.5,0.6,0.7,0.8]}
gsearch1 = GridSearchCV(estimator = XGBClassifier(max_depth=3,
    learning_rate =0.01, n_estimators=140,       
    min_child_weight=1,objective= 'binary:logistic', nthread=4,seed=27),       
    param_grid=param_grid,cv=5)
gsearch1.fit(X,y)
print(gsearch1.best_params_,gsearch1.best_score_)

--------------------------------------------------------------------------------------------------------------------------------

相比于xgboost中的方式，会有些参数名字上的修改，不过影响不大：
    
    1、eta -> learning_rate 
    2、lambda -> reg_lambda 
    3、alpha -> reg_alpha

调参记录:

    *boostergbtree 树模型做为基分类器（默认）
    *gbliner 线性模型做为基分类器
    *n_jobs  并行线程数
    *silentsilent=0时，不输出中间过程（默认）silent=1时，输出中间过程
    *nthreadnthread=-1时，使用全部CPU进行并行运算（默认）nthread=1时，使用1个CPU进行运算。
    *scale_pos_weight正样本的权重，在二分类任务中，当正负样本比例失衡时，设置正样本的权重，模型效果更好。例如，当正负样本比例为1:10时scale_pos_weight=10。
    *n_estimatores含义：总共迭代的次数，即决策树的个数调参：
    *max_depth含义：树的深度，默认值为6，典型值3-10。调参：值越大，越容易过拟合；值越小，越容易欠拟合。
    *min_child_weight含义：默认值为1,。调参：值越大，越容易欠拟合；值越小，越容易过拟合（值较大时，避免模型学习到局部的特殊样本）。
    *subsample含义：训练每棵树时，使用的数据占全部训练集的比例。默认值为1，典型值为0.5-1。调参：防止overfitting。
    *colsample_bytree含义：训练每棵树时，使用的特征占全部特征的比例。默认值为1，典型值为0.5-1。调参：防止overfitting。
    *learning_rate含义：学习率，控制每次迭代更新权重时的步长，默认0.3。调参：值越小，训练越慢。典型值为0.01-0.2。
    *gamma惩罚项系数，指定节点分裂所需的最小损失函数下降值。调参：
    *alphaL1正则化系数，默认为1lambdaL2正则化系数，默认为1
参考文献：https://blog.csdn.net/han_xiaoyang/article/details/52665396

# ----------------------         2.Catboost模型       -------------------------

In [185]:
from  catboost  import  CatBoostClassifier,CatBoostRegressor,Pool
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import roc_auc_score
print("start：********************************")
start = time.time()
N = 5
skf = StratifiedKFold(n_splits=N,shuffle=True,random_state=2018)

auc_cv = []
pred_cv = []
for k,(train_in,test_in) in enumerate(skf.split(X,y)):
    X_train,X_test,y_train,y_test = X[train_in],X[test_in],\
                                    y[train_in],y[test_in]    
    model=CatBoostClassifier(depth=6,custom_loss=['AUC'],
                            logging_level='Silent',learning_rate=0.01,
                            iterations=1000,l2_leaf_reg=2,   
                            od_wait=20)
    model.fit(X_train,y_train)
    predict=model.predict_proba(X_test)
    predict=[i[1]  for i in predict] #提取正例概率，用于计算AUC面积值。
    #print('预测的predict:',predict)
    tmp_auc = roc_auc_score(y_test,predict)
    auc_cv.append(tmp_auc)
    print("valid auc:",tmp_auc)
    # test
    pred = model.predict_proba(test_data)
    pred_cv.append(pred) 
    
    
# K交叉验证的平均分数 
print('the cv information:')
print(auc_cv)
print('cv mean score',np.mean(auc_cv))

end = time.time()
print("......................run with time: ",(end - start) / 60.0 )
print("over:*********************************")   
    

    


start：********************************
valid auc: 0.8048152672830289
valid auc: 0.7965469571294018
valid auc: 0.8578651799187758
valid auc: 0.8336726116326882
valid auc: 0.7842803519596371
the cv information:
[0.8048152672830289, 0.7965469571294018, 0.8578651799187758, 0.8336726116326882, 0.7842803519596371]
cv mean score 0.8154360735847064
......................run with time:  2.953768841425578
over:*********************************


效果记录：

     [1]使用如下参数，线下效果是0.8086793696648483   （可以发现其与lightGBM的方式是很不同的）
           depth=4,custom_loss=['AUC'],
           logging_level='Silent',
           learning_rate=0.01,
           iterations=300,
           l2_leaf_reg=2,   
           od_wait=20
     [2]当我们使用调参调出来的结果，线下成绩则为0.8039473166164178，对应参数如下：
           depth=2,custom_loss=['AUC'],
           logging_level='Silent',
           learning_rate=0.01,
           iterations=300,
           l2_leaf_reg=2,   
           od_wait=20
    [3]当增加迭代次数，扩大树深度之后可以发现线下提升到0.8154360735847064
           depth=6,custom_loss=['AUC'],
           logging_level='Silent',
           learning_rate=0.01,    
           iterations=1000,
           l2_leaf_reg=2,   
           od_wait=20

In [178]:
#catboost调参
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.model_selection import GridSearchCV
from catboost import CatBoostClassifier
#使用网格搜索找最佳的参数
param_grid = {'depth':[i for i in range(2,8)],'learning_rate':[0.01,0.02,0.03,0.04,],'l2_leaf_reg':[2,3,4,5]}
gsearch1 = GridSearchCV(estimator = CatBoostClassifier(
    learning_rate =0.01, n_estimators=140),       
    param_grid=param_grid,cv=5)
gsearch1.fit(X,y)
print(gsearch1.best_params_,gsearch1.best_score_)

0:	learn: 0.6802197	total: 22.3ms	remaining: 3.1s
1:	learn: 0.6681185	total: 38.7ms	remaining: 2.67s
2:	learn: 0.6561726	total: 55.9ms	remaining: 2.55s
3:	learn: 0.6443670	total: 72.5ms	remaining: 2.46s
4:	learn: 0.6332805	total: 87.8ms	remaining: 2.37s
5:	learn: 0.6220564	total: 105ms	remaining: 2.34s
6:	learn: 0.6114853	total: 119ms	remaining: 2.27s
7:	learn: 0.6011442	total: 134ms	remaining: 2.22s
8:	learn: 0.5907976	total: 152ms	remaining: 2.21s
9:	learn: 0.5805469	total: 167ms	remaining: 2.18s
10:	learn: 0.5706808	total: 186ms	remaining: 2.18s
11:	learn: 0.5611269	total: 201ms	remaining: 2.15s
12:	learn: 0.5522080	total: 220ms	remaining: 2.15s
13:	learn: 0.5431292	total: 236ms	remaining: 2.12s
14:	learn: 0.5346887	total: 254ms	remaining: 2.12s
15:	learn: 0.5262272	total: 269ms	remaining: 2.08s
16:	learn: 0.5182305	total: 284ms	remaining: 2.06s
17:	learn: 0.5103582	total: 299ms	remaining: 2.03s
18:	learn: 0.5024521	total: 313ms	remaining: 2s
19:	learn: 0.4950869	total: 329ms	remain

24:	learn: 0.4425835	total: 400ms	remaining: 1.84s
25:	learn: 0.4358367	total: 422ms	remaining: 1.85s
26:	learn: 0.4285699	total: 438ms	remaining: 1.83s
27:	learn: 0.4224196	total: 453ms	remaining: 1.81s
28:	learn: 0.4162998	total: 469ms	remaining: 1.79s
29:	learn: 0.4103719	total: 488ms	remaining: 1.79s
30:	learn: 0.4045821	total: 508ms	remaining: 1.78s
31:	learn: 0.3984180	total: 524ms	remaining: 1.77s
32:	learn: 0.3930121	total: 538ms	remaining: 1.75s
33:	learn: 0.3875491	total: 554ms	remaining: 1.73s
34:	learn: 0.3823943	total: 569ms	remaining: 1.71s
35:	learn: 0.3767578	total: 590ms	remaining: 1.7s
36:	learn: 0.3718963	total: 606ms	remaining: 1.69s
37:	learn: 0.3668611	total: 621ms	remaining: 1.67s
38:	learn: 0.3622354	total: 637ms	remaining: 1.65s
39:	learn: 0.3577207	total: 651ms	remaining: 1.63s
40:	learn: 0.3533216	total: 666ms	remaining: 1.61s
41:	learn: 0.3485707	total: 681ms	remaining: 1.59s
42:	learn: 0.3445731	total: 696ms	remaining: 1.57s
43:	learn: 0.3406047	total: 711m

45:	learn: 0.3418575	total: 754ms	remaining: 1.54s
46:	learn: 0.3384198	total: 773ms	remaining: 1.53s
47:	learn: 0.3350904	total: 787ms	remaining: 1.51s
48:	learn: 0.3318240	total: 802ms	remaining: 1.49s
49:	learn: 0.3284285	total: 816ms	remaining: 1.47s
50:	learn: 0.3253672	total: 830ms	remaining: 1.45s
51:	learn: 0.3214405	total: 845ms	remaining: 1.43s
52:	learn: 0.3173651	total: 860ms	remaining: 1.41s
53:	learn: 0.3139408	total: 877ms	remaining: 1.4s
54:	learn: 0.3105031	total: 892ms	remaining: 1.38s
55:	learn: 0.3079453	total: 907ms	remaining: 1.36s
56:	learn: 0.3053919	total: 922ms	remaining: 1.34s
57:	learn: 0.3024512	total: 940ms	remaining: 1.33s
58:	learn: 0.2995850	total: 960ms	remaining: 1.32s
59:	learn: 0.2969124	total: 978ms	remaining: 1.3s
60:	learn: 0.2940058	total: 992ms	remaining: 1.28s
61:	learn: 0.2913606	total: 1.01s	remaining: 1.27s
62:	learn: 0.2891629	total: 1.02s	remaining: 1.25s
63:	learn: 0.2866114	total: 1.04s	remaining: 1.23s
64:	learn: 0.2843062	total: 1.05s

71:	learn: 0.1622810	total: 1.14s	remaining: 1.08s
72:	learn: 0.1603666	total: 1.16s	remaining: 1.06s
73:	learn: 0.1584717	total: 1.18s	remaining: 1.05s
74:	learn: 0.1566048	total: 1.19s	remaining: 1.03s
75:	learn: 0.1547262	total: 1.2s	remaining: 1.01s
76:	learn: 0.1531875	total: 1.22s	remaining: 997ms
77:	learn: 0.1514368	total: 1.23s	remaining: 980ms
78:	learn: 0.1496648	total: 1.25s	remaining: 964ms
79:	learn: 0.1482179	total: 1.26s	remaining: 947ms
80:	learn: 0.1465959	total: 1.28s	remaining: 931ms
81:	learn: 0.1450856	total: 1.29s	remaining: 915ms
82:	learn: 0.1436507	total: 1.31s	remaining: 901ms
83:	learn: 0.1421376	total: 1.33s	remaining: 885ms
84:	learn: 0.1409405	total: 1.34s	remaining: 869ms
85:	learn: 0.1397412	total: 1.36s	remaining: 852ms
86:	learn: 0.1383608	total: 1.37s	remaining: 835ms
87:	learn: 0.1372143	total: 1.39s	remaining: 821ms
88:	learn: 0.1361541	total: 1.4s	remaining: 804ms
89:	learn: 0.1350638	total: 1.42s	remaining: 789ms
90:	learn: 0.1340140	total: 1.44s

98:	learn: 0.2165382	total: 2.09s	remaining: 867ms
99:	learn: 0.2153362	total: 2.11s	remaining: 845ms
100:	learn: 0.2142790	total: 2.13s	remaining: 824ms
101:	learn: 0.2132156	total: 2.16s	remaining: 805ms
102:	learn: 0.2123951	total: 2.18s	remaining: 783ms
103:	learn: 0.2111781	total: 2.21s	remaining: 765ms
104:	learn: 0.2104292	total: 2.23s	remaining: 744ms
105:	learn: 0.2096576	total: 2.26s	remaining: 724ms
106:	learn: 0.2088132	total: 2.29s	remaining: 705ms
107:	learn: 0.2079122	total: 2.31s	remaining: 684ms
108:	learn: 0.2069537	total: 2.33s	remaining: 663ms
109:	learn: 0.2058621	total: 2.35s	remaining: 642ms
110:	learn: 0.2050390	total: 2.38s	remaining: 621ms
111:	learn: 0.2044201	total: 2.4s	remaining: 599ms
112:	learn: 0.2036353	total: 2.42s	remaining: 578ms
113:	learn: 0.2029452	total: 2.44s	remaining: 556ms
114:	learn: 0.2021129	total: 2.47s	remaining: 536ms
115:	learn: 0.2012896	total: 2.5s	remaining: 517ms
116:	learn: 0.2004056	total: 2.52s	remaining: 496ms
117:	learn: 0.19

...

57:	learn: 0.1886825	total: 2.28s	remaining: 3.23s
58:	learn: 0.1883531	total: 2.32s	remaining: 3.19s
59:	learn: 0.1880501	total: 2.37s	remaining: 3.16s
60:	learn: 0.1878539	total: 2.41s	remaining: 3.13s
61:	learn: 0.1875246	total: 2.46s	remaining: 3.1s
62:	learn: 0.1869890	total: 2.5s	remaining: 3.06s
63:	learn: 0.1867591	total: 2.54s	remaining: 3.02s
64:	learn: 0.1863626	total: 2.58s	remaining: 2.98s
65:	learn: 0.1860382	total: 2.64s	remaining: 2.96s
66:	learn: 0.1858642	total: 2.68s	remaining: 2.92s
67:	learn: 0.1856123	total: 2.75s	remaining: 2.91s
68:	learn: 0.1854263	total: 2.79s	remaining: 2.88s
69:	learn: 0.1852061	total: 2.83s	remaining: 2.83s
70:	learn: 0.1849716	total: 2.87s	remaining: 2.79s
71:	learn: 0.1846805	total: 2.92s	remaining: 2.76s
72:	learn: 0.1843045	total: 2.96s	remaining: 2.72s
73:	learn: 0.1839756	total: 3s	remaining: 2.68s
74:	learn: 0.1837551	total: 3.05s	remaining: 2.65s
75:	learn: 0.1834523	total: 3.11s	remaining: 2.62s
76:	learn: 0.1831234	total: 3.16s	re

80:	learn: 0.1568399	total: 3.55s	remaining: 2.59s
81:	learn: 0.1564859	total: 3.6s	remaining: 2.55s
82:	learn: 0.1564520	total: 3.63s	remaining: 2.5s
83:	learn: 0.1564262	total: 3.67s	remaining: 2.44s
84:	learn: 0.1563463	total: 3.71s	remaining: 2.4s
85:	learn: 0.1562077	total: 3.75s	remaining: 2.35s
86:	learn: 0.1561619	total: 3.77s	remaining: 2.3s
87:	learn: 0.1559101	total: 3.82s	remaining: 2.26s
88:	learn: 0.1557640	total: 3.86s	remaining: 2.21s
89:	learn: 0.1556259	total: 3.9s	remaining: 2.17s
90:	learn: 0.1554782	total: 3.95s	remaining: 2.13s
91:	learn: 0.1553460	total: 3.99s	remaining: 2.08s
92:	learn: 0.1551432	total: 4.04s	remaining: 2.04s
93:	learn: 0.1549006	total: 4.08s	remaining: 2s
94:	learn: 0.1548827	total: 4.12s	remaining: 1.95s
95:	learn: 0.1547160	total: 4.17s	remaining: 1.91s
96:	learn: 0.1545989	total: 4.19s	remaining: 1.86s
97:	learn: 0.1545820	total: 4.23s	remaining: 1.81s
98:	learn: 0.1542569	total: 4.28s	remaining: 1.77s
99:	learn: 0.1541150	total: 4.32s	remai

101:	learn: 0.1527783	total: 4.42s	remaining: 1.65s
102:	learn: 0.1526330	total: 4.47s	remaining: 1.61s
103:	learn: 0.1524717	total: 4.52s	remaining: 1.56s
104:	learn: 0.1523611	total: 4.56s	remaining: 1.52s
105:	learn: 0.1522860	total: 4.6s	remaining: 1.48s
106:	learn: 0.1520873	total: 4.64s	remaining: 1.43s
107:	learn: 0.1519773	total: 4.68s	remaining: 1.39s
108:	learn: 0.1519679	total: 4.7s	remaining: 1.34s
109:	learn: 0.1518867	total: 4.74s	remaining: 1.29s
110:	learn: 0.1518194	total: 4.78s	remaining: 1.25s
111:	learn: 0.1517269	total: 4.83s	remaining: 1.21s
112:	learn: 0.1516059	total: 4.87s	remaining: 1.16s
113:	learn: 0.1515029	total: 4.92s	remaining: 1.12s
114:	learn: 0.1514018	total: 4.96s	remaining: 1.08s
115:	learn: 0.1513052	total: 5s	remaining: 1.03s
116:	learn: 0.1512211	total: 5.05s	remaining: 993ms
117:	learn: 0.1511212	total: 5.09s	remaining: 950ms
118:	learn: 0.1509181	total: 5.14s	remaining: 907ms
119:	learn: 0.1508327	total: 5.18s	remaining: 863ms
120:	learn: 0.150

122:	learn: 0.0746514	total: 5.46s	remaining: 754ms
123:	learn: 0.0746228	total: 5.5s	remaining: 710ms
124:	learn: 0.0745985	total: 5.54s	remaining: 665ms
125:	learn: 0.0744932	total: 5.58s	remaining: 620ms
126:	learn: 0.0742539	total: 5.65s	remaining: 578ms
127:	learn: 0.0742123	total: 5.69s	remaining: 534ms
128:	learn: 0.0739617	total: 5.75s	remaining: 490ms
129:	learn: 0.0738829	total: 5.8s	remaining: 446ms
130:	learn: 0.0738462	total: 5.84s	remaining: 401ms
131:	learn: 0.0736384	total: 5.89s	remaining: 357ms
132:	learn: 0.0735600	total: 5.95s	remaining: 313ms
133:	learn: 0.0734428	total: 6s	remaining: 269ms
134:	learn: 0.0732873	total: 6.06s	remaining: 224ms
135:	learn: 0.0731945	total: 6.11s	remaining: 180ms
136:	learn: 0.0731039	total: 6.17s	remaining: 135ms
137:	learn: 0.0729765	total: 6.22s	remaining: 90.2ms
138:	learn: 0.0729556	total: 6.27s	remaining: 45.1ms
139:	learn: 0.0728662	total: 6.32s	remaining: 0us
0:	learn: 0.6349400	total: 52.8ms	remaining: 7.34s
1:	learn: 0.581757

9:	learn: 0.5688279	total: 244ms	remaining: 3.17s
10:	learn: 0.5580526	total: 263ms	remaining: 3.09s
11:	learn: 0.5474497	total: 283ms	remaining: 3.02s
12:	learn: 0.5371142	total: 303ms	remaining: 2.96s
13:	learn: 0.5268253	total: 322ms	remaining: 2.9s
14:	learn: 0.5169070	total: 341ms	remaining: 2.84s
15:	learn: 0.5079659	total: 362ms	remaining: 2.81s
16:	learn: 0.4989231	total: 389ms	remaining: 2.81s
17:	learn: 0.4903441	total: 412ms	remaining: 2.79s
18:	learn: 0.4815195	total: 435ms	remaining: 2.77s
19:	learn: 0.4735922	total: 456ms	remaining: 2.74s
20:	learn: 0.4658415	total: 477ms	remaining: 2.7s
21:	learn: 0.4583365	total: 495ms	remaining: 2.66s
22:	learn: 0.4507763	total: 516ms	remaining: 2.63s
23:	learn: 0.4436902	total: 541ms	remaining: 2.61s
24:	learn: 0.4360781	total: 568ms	remaining: 2.61s
25:	learn: 0.4294091	total: 589ms	remaining: 2.58s
26:	learn: 0.4228517	total: 610ms	remaining: 2.55s
27:	learn: 0.4165451	total: 630ms	remaining: 2.52s
28:	learn: 0.4102116	total: 656ms	

调参说明：https://blog.csdn.net/AiirrrrYee/article/details/78224232
参数解释：
    nan_mode (string): 处理输入数据中缺失值的方法，包括Forbidden(禁止存在缺失)，Min(用最小值补)，Max(用最大值补)。默认Min。
    calc_feature_importance (bool): 是否计算特征重要性。默认True。
    fold_permutation_block_size (int): 在数据随机排列前分块，值越小越慢。默认1。
    ignored_features (list): 忽略数据集中的某些特征。默认None。
    use_best_model (bool): 设置此参数时，需要提供测试数据，树的个数通过训练参数和优化loss function获得。默认False。
    loss_function (string/ object): 支持的有RMSE, Logloss, MAE, CrossEntropy, Quantile, LogLinQuantile, Multiclass, MultiClassOneVsAll, MAPE,  Poisson。默认Logloss。
    custom_loss (object):  训练过程中损失函数的值。默认None。（RMSE  Logloss  MAE  CrossEntropy Recall Precision F1 Accuracy AUC R2）
    eval_metric (string):  用于过拟合检验（设置True）和最佳模型选择（设置True）的loss function，用于优化。（RMSE Logloss MAE CrossEntropy Recall Precision F1 Accuracy AUC R2）
    iterations (int): 最大树数。默认500。
    border (float): 用于二分类／使用Logloss function中，大于border认为是正样本。默认0.5。
    gradient_iterations (int): 梯度下降的步数。默认1。
    depth (int): 树深，最大16，建议在1到10之间。默认6。
    learning_rate (float): 学习率。默认0.03。
    rsm (float [0; 1]): 随机子空间（Random subspace method）。默认1。
    partition_random_seed (int): 随机种子。默认None，每次训练随机选择。
    leaf_estimation_method (string): 计算叶子值的方法，Newton/ Gradient。默认Gradient。
    l2_leaf_reg (int): l2正则参数。默认3
    has_time (bool): 在将categorical features转化为numerical features和选择树结构时，顺序选择输入数据。默认False（随机）。
    priors (string): 训练过程中指定先验。默认None。
    feature_priors (list): 在将categorical features转化为numerical features时，指定先验。
    name (string): 在可视化工具中的实验名称。默认experiment。
    fold_len_multiplier (float): folds长度系数。设置大于1的参数，在参数较小时获得最佳结果。默认2。
    approx_on_full_history (bool): 计算近似值，False：使用1／fold_len_multiplier计算；True：使用fold中前面所有行计算。默认False。
    class_weights (list): 类别的权重。默认None。
    classes_count (int): 类别label的上限。默认：类别label最大值＋1。
    one_hot_max_size (bool): 如果feature包含的不同值的数目超过了指定值，将feature转化为float。默认False
    random_strength (float): 分数标准差乘数。默认1。
    bagging_temperature (float): 贝叶斯套袋控制强度，区间[0, 1]。默认1。
    one_hot_max_size=2: 对于某些变量进行one-hot编码

# ----------------------         3.GBDT模型       -------------------------

In [191]:
from sklearn.datasets import make_hastie_10_2
from sklearn.ensemble import GradientBoostingClassifier

from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import roc_auc_score
print("start：********************************")
start = time.time()

N = 5
skf = StratifiedKFold(n_splits=N,shuffle=True,random_state=2018)

auc_cv = []
pred_cv = []
for k,(train_in,test_in) in enumerate(skf.split(X,y)):
    X_train,X_test,y_train,y_test = X[train_in],X[test_in],\
                                    y[train_in],y[test_in]   
    
    clf = GradientBoostingClassifier(n_estimators=300, learning_rate=0.01,
         max_depth=8, random_state=0,min_weight_fraction_leaf=0.2)
    clf.fit(X_train, y_train)
    predict=clf.predict_proba(X_test)
    predict=[i[1]  for i in predict]
    print('......................')
    #print(predict)
    tmp_auc = roc_auc_score(y_test,predict)
    auc_cv.append(tmp_auc)
    print("valid auc:",tmp_auc)
    #clf.score(X_test, y_test) 
    
# K交叉验证的平均分数 
print('the cv information:')
print(auc_cv)
print('cv mean score',np.mean(auc_cv))

end = time.time()
print("......................run with time: ",(end - start) / 60.0 )
print("over:*********************************") 

start：********************************
......................
valid auc: 0.7747650935855089
......................
valid auc: 0.7740862273265884
......................
valid auc: 0.8281504775215468
......................
valid auc: 0.813748873292215
......................
valid auc: 0.7736222765932659
the cv information:
[0.7747650935855089, 0.7740862273265884, 0.8281504775215468, 0.813748873292215, 0.7736222765932659]
cv mean score 0.792874589663825
......................run with time:  1.097914719581604
over:*********************************


效果日志：


     [1]初步我们适用于一定的参数进行效果的展示，效果为0.7814034804077632，参数为：
           n_estimators=160, 
           learning_rate=0.01,
           max_depth=8, 
           random_state=0,
           min_weight_fraction_leaf=0.2

In [ ]:
#GBDT调参日志
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import GradientBoostingClassifier
#使用网格搜索找最佳的参数
param_grid = {'max_depth':range(3,14,2),'min_samples_split':range(100,801,200),'min_weight_fraction_leaf':[0.1,0.3,0.5]}
gsearch1 = GridSearchCV(estimator = GradientBoostingClassifier(
    learning_rate =0.01, n_estimators=140),       
    param_grid=param_grid,cv=5)
gsearch1.fit(X,y)
print(gsearch1.best_params_,gsearch1.best_score_)

gbdt的参数说明如下：
       
        1) 划分时考虑的最大特征数max_features: 可以使用很多种类型的值，默认是"None",意味着划分时考虑所有的特征数；如果是"log2"意味着划分时最多考虑$log_2N$个特征；如果是"sqrt"或者"auto"意味着划分时最多考虑$\sqrt{N}$个特征。如果是整数，代表考虑的特征绝对数。如果是浮点数，代表考虑特征百分比，即考虑（百分比xN）取整后的特征数。其中N为样本总特征数。一般来说，如果样本特征数不多，比如小于50，我们用默认的"None"就可以了，如果特征数非常多，我们可以灵活使用刚才描述的其他取值来控制划分时考虑的最大特征数，以控制决策树的生成时间。
        
        2) 决策树最大深度max_depth: 默认可以不输入，如果不输入的话，决策树在建立子树的时候不会限制子树的深度。一般来说，数据少或者特征少的时候可以不管这个值。如果模型样本量多，特征也多的情况下，推荐限制这个最大深度，具体的取值取决于数据的分布。常用的可以取值10-100之间。
　　　　
    
        3) 内部节点再划分所需最小样本数min_samples_split: 这个值限制了子树继续划分的条件，如果某节点的样本数少于min_samples_split，则不会继续再尝试选择最优特征来进行划分。 默认是2.如果样本量不大，不需要管这个值。如果样本量数量级非常大，则推荐增大这个值。
　　　　
        4) 叶子节点最少样本数min_samples_leaf: 这个值限制了叶子节点最少的样本数，如果某叶子节点数目小于样本数，则会和兄弟节点一起被剪枝。 默认是1,可以输入最少的样本数的整数，或者最少样本数占样本总数的百分比。如果样本量不大，不需要管这个值。如果样本量数量级非常大，则推荐增大这个值。
　　　　
    
        5）叶子节点最小的样本权重和min_weight_fraction_leaf：这个值限制了叶子节点所有样本权重和的最小值，如果小于这个值，则会和兄弟节点一起被剪枝。 默认是0，就是不考虑权重问题。一般来说，如果我们有较多样本有缺失值，或者分类树样本的分布类别偏差很大，就会引入样本权重，这时我们就要注意这个值了。
       
        6) 最大叶子节点数max_leaf_nodes: 通过限制最大叶子节点数，可以防止过拟合，默认是"None”，即不限制最大的叶子节点数。如果加了限制，算法会建立在最大叶子节点数内最优的决策树。如果特征不多，可以不考虑这个值，但是如果特征分成多的话，可以加以限制，具体的值可以通过交叉验证得到。
　　　　
        7) 节点划分最小不纯度**min_impurity_split: ** 这个值限制了决策树的增长，如果某节点的不纯度(基于基尼系数，均方差)小于这个阈值，则该节点不再生成子节点。即为叶子节点 。一般不推荐改动默认值1e-7。


![title](image/pic1.png)

# ----------------------         4.Lasso模型       -------------------------


In [192]:
from sklearn.linear_model import Lasso
from sklearn.datasets import make_hastie_10_2
from sklearn.ensemble import GradientBoostingClassifier

from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import roc_auc_score
print("start：********************************")
start = time.time()

N = 5
skf = StratifiedKFold(n_splits=N,shuffle=True,random_state=2018)

auc_cv = []
pred_cv = []
for k,(train_in,test_in) in enumerate(skf.split(X,y)):
    X_train,X_test,y_train,y_test = X[train_in],X[test_in],\
                                    y[train_in],y[test_in] 
    alpha=0.1
    lasso=Lasso(alpha=alpha)
    y_pred_lasso=lasso.fit(X_train,y_train).predict(X_test)
    tmp_auc = roc_auc_score(y_test,y_pred_lasso)
    auc_cv.append(tmp_auc)
    print("valid auc:",tmp_auc)
    #clf.score(X_test, y_test) 
    
# K交叉验证的平均分数 
print('the cv information:')
print(auc_cv)
print('cv mean score',np.mean(auc_cv))

end = time.time()
print("......................run with time: ",(end - start) / 60.0 )
print("over:*********************************") 

start：********************************
valid auc: 0.6777471104877105
valid auc: 0.6659779823575284
valid auc: 0.7057646927759041
valid auc: 0.7227121502142011
valid auc: 0.6957610848542872
the cv information:
[0.6777471104877105, 0.6659779823575284, 0.7057646927759041, 0.7227121502142011, 0.6957610848542872]
cv mean score 0.6935926041379263
......................run with time:  0.01593423287073771
over:*********************************


# ----------------------         5.SVM模型       -------------------------

In [202]:
from sklearn.svm import SVC
from sklearn.linear_model import Lasso
from sklearn.datasets import make_hastie_10_2
from sklearn.ensemble import GradientBoostingClassifier
import sys,random,os
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import roc_auc_score
print("start：********************************")
start = time.time()

N = 5
skf = StratifiedKFold(n_splits=N,shuffle=True,random_state=2018)

auc_cv = []
pred_cv = []
for k,(train_in,test_in) in enumerate(skf.split(X,y)):
    X_train,X_test,y_train,y_test = X[train_in],X[test_in],\
                                    y[train_in],y[test_in] 

    random_seed = list(range(2016,2046))
    C = [i/10.0 for i in range(10,40)]
    gamma = [i/1000.0 for i in range(1,31)]
    #进行列表的打乱
    random.shuffle(random_seed)
    random.shuffle(C)
    random.shuffle(gamma)
    
    clf = SVC(C=C[1],kernel='rbf',gamma=gamma[1],probability=True,cache_size=7000,class_weight='balanced',verbose=True,random_state=random_seed[1])
    clf.fit(X,y)
    pred = clf.predict_proba(X_test)
    predict = pred[:,1]
    
    print('......................')
    #print(predict)
    tmp_auc = roc_auc_score(y_test,predict)
    auc_cv.append(tmp_auc)
    print("valid auc:",tmp_auc)
    #clf.score(X_test, y_test) 
    
# K交叉验证的平均分数 
print('the cv information:')
print(auc_cv)
print('cv mean score',np.mean(auc_cv))

end = time.time()
print("......................run with time: ",(end - start) / 60.0 )
print("over:*********************************") 

start：********************************
[LibSVM]......................
valid auc: 0.8954898973902639
[LibSVM]......................
valid auc: 0.9697156138911676
[LibSVM]......................
valid auc: 0.98171188689373
[LibSVM]......................
valid auc: 0.9876669806256899
[LibSVM]......................
valid auc: 0.912906706381168
the cv information:
[0.8954898973902639, 0.9697156138911676, 0.98171188689373, 0.9876669806256899, 0.912906706381168]
cv mean score 0.9494982170364039
......................run with time:  28.818184351921083
over:*********************************


# 四.模型融合

# 附录1：尝试点日志

# 附录2：上分点日志

# 附录3：疑问点

   1.对均值填充后的列  不做rank排序
      
          原因在于排序特征对异常数据有更强的鲁棒性，使得模型更加稳定，降低过拟合的风险，但均值填充的特征已经破坏了排序性，那样排序下来的结果是不行的。而且因为这是非常重要的特征，如果直接排序下来会影响其数值意义，为了稳定而丢失数据本质这样很不值得
      
   2.使用xgboost和lightGBM预测时可以直接使用predict，这样得到的是概率值，而在catboost、GBDT这些模型中则一定要使用predict_proba才能得到概率，这就是不同的方式？   看来自己对基本的任务机制就不太明白哎，后来会计算roc_auc_score这个函数下的结果
   
   3.发现一个有趣的问题，对于二分类问题，发现使用模型的，xgboost下的train然后predict预测概率，和用XGBClassifier里的predict、predict_prob这三种形式拿来做预测的方法是非常不同的，直接的xgboost下的predict得到的是最正式的，用其计算AUC效果最好，而在XGBClassifier分类器下面得到的predict得到的标签0或者1、而predict_prob得到的是一定的概率，是一种很大的概率值。为什么呢？
  
    答案：可算是明白了，其实xgboost下的predict和XGBClassifier下的predict_prob其实是同一种方式，只不过predict_prob会得到分类为0的概率和分类为1的概率，因此当我们使用 model.predict_proba(X_test)[:][1]定位到正例概率即可。   但是发现predict效果更好，应该是classifer没有调参的原因吧。
   4.进行调参要注意的事情（比如GBDT）
   
    针对不同情况其调参方式是非常需要注意的，比如下面如果针对样本不均衡问题来调参时候，注意一定要 先调整'叶节点最小样本数'min_samples_leaf之后分裂所需最小样本数”（min_samples_split）、最后才能确定最大深度。
    而反面的例子：直接先调试“最大深度”（max_depth），会发现其会保持默认值3作为最优解，而后面的调参中，“分裂所需最小样本数”（min_samples_split）、“叶节点最小样本数”（min_samples_leaf）再怎么调都没有很大作用。这是因为，正例样本远远小于反例，所以在低深度时，子模型就可能已经对正例过拟合了。
    所以啊，调参的调节先后关系是很重要的，要明白其意义，当然如果你将所以组合都穷举出来当然是最保险的
    
   5.在模型的效果稳定性方面
   
      方法就是对数值进行精处理，包括排序特征与离散特征，对异常数据更鲁棒，分箱处理也是一样，让区分度更小些，放置特别异常点导致的深度误导。


# 附录4：参数
